In [1]:
import pandas as pd
import numpy as np
import os
import re
from tqdm import tqdm
from tqdm import tnrange, tqdm_notebook, tqdm_pandas
from SPARQLWrapper import SPARQLWrapper, JSON
tqdm.pandas()
# pd.set_option('display.max_columns', None)
# pd.set_option('display.max_rows', None)

C:\Anaconda3\lib\site-packages\tqdm\std.py:648: FutureWarning: The Panel class is removed from pandas. Accessing it from the top-level namespace will also be removed in the next version
  from pandas import Panel


In [2]:
target_dir = './dataset/Round1/targets'
gt_dir = 'C:/Users/Marcin Borzymowski/OneDrive - student.put.poznan.pl/_studia/semestr7/Bąk/dataset/Round1/gt'
tables_dir = 'C:/Users/Marcin Borzymowski/OneDrive - student.put.poznan.pl/_studia/semestr7/Bąk/dataset/Round 1/tables'

#### GET GT DF

In [3]:
df_gt = pd.read_csv("CTA_Round1_gt.csv", 
                        header=None,
                        names=['table_id', 'column_id', 'dbpednia_class'],
                        dtype={'column_id': np.int8})

In [4]:
df_gt

table_id  column_id  \
0     58891288_0_1117541047012405958          1   
1      8468806_0_4382447409703007384          1   
2      50245608_0_871275842592178099          0   
3      14067031_0_559833072073397908          1   
4      8286121_0_8471791395229161598          0   
..                               ...        ...   
115   66009064_0_9148652238372261251          2   
116   21362676_0_6854186738074119688          1   
117   39107734_2_2329160387535788734          2   
118  29414811_13_8724394428539174350          1   
119   75367212_2_2745466355267233390          0   

                             dbpednia_class  
0          http://dbpedia.org/ontology/Film  
1          http://dbpedia.org/ontology/Lake  
2          http://dbpedia.org/ontology/Film  
3      http://dbpedia.org/ontology/Language  
4       http://dbpedia.org/ontology/Country  
..                                      ...  
115  http://dbpedia.org/ontology/SportsTeam  
116        http://dbpedia.org/ontology/Film  
117        http://dbpedia.org/ontology/City  
118   http://dbpedia.org/ontology/VideoGame  
119   http://dbpedia.org/ontology/VideoGame  

[120 rows x 3 columns]

In [5]:
def remove_wrong_gts(df):
    wrong_gt_ids = []
    
    for index, row in tqdm(df.iterrows()):
        try:
            pd.read_csv(os.path.join(tables_dir, row['table_id'] + ".csv")) 
        except:
            wrong_gt_ids.append(index)
    return df.drop(wrong_gt_ids).reset_index(drop=True)

In [6]:
df_gt = remove_wrong_gts(df_gt)

120it [00:00, 569.76it/s]


#### Preporcess DF

In [7]:
def preporcess_item(word):
    word = re.sub('[^A-Za-z0-9 ]+', '', word)
    word = re.sub(' {1,}', '_', word)
    word = word.replace("__", "_")
    
    return word

#### Get column items

In [8]:
column_items = []
def get_column_items(row):
    global column_items
    table_id = row["table_id"]
    column_id = row["column_id"]
    
    df = pd.read_csv(os.path.join(tables_dir, table_id + ".csv"))
    cells = []
    column = df.iloc[ : , column_id]
    for i, value in column.items():
        value = preporcess_item(str(value))
        cells.append(value)
    column_items.append(cells)

In [9]:
df_gt.progress_apply(get_column_items, axis=1)

100%|███████████████████████████████████████████████████████████████████████████████| 120/120 [00:00<00:00, 418.12it/s]


0      None
1      None
2      None
3      None
4      None
       ... 
115    None
116    None
117    None
118    None
119    None
Length: 120, dtype: object

In [11]:
# for s in column_items:
#     print(*s)

#### COLUMN ITEMS -> ADD DB CLASSES TO EACH ITEM

In [12]:
def get_ontology_classes(item):
    respond = []
    sparql = SPARQLWrapper("http://dbpedia.org/sparql")
    sparql.setQuery("select distinct ?class where { dbr:"+item+" a ?class.}")
    sparql.setReturnFormat(JSON)
    results = sparql.query().convert()
    
    respond.append(item)
    respond.append([result["class"]["value"] for result in results["results"]["bindings"] 
            if 'http://dbpedia.org/ontology' in result["class"]["value"]])
    
    return respond

In [15]:
df_gt

table_id  column_id  \
0     58891288_0_1117541047012405958          1   
1      8468806_0_4382447409703007384          1   
2      50245608_0_871275842592178099          0   
3      14067031_0_559833072073397908          1   
4      8286121_0_8471791395229161598          0   
..                               ...        ...   
115   66009064_0_9148652238372261251          2   
116   21362676_0_6854186738074119688          1   
117   39107734_2_2329160387535788734          2   
118  29414811_13_8724394428539174350          1   
119   75367212_2_2745466355267233390          0   

                             dbpednia_class  
0          http://dbpedia.org/ontology/Film  
1          http://dbpedia.org/ontology/Lake  
2          http://dbpedia.org/ontology/Film  
3      http://dbpedia.org/ontology/Language  
4       http://dbpedia.org/ontology/Country  
..                                      ...  
115  http://dbpedia.org/ontology/SportsTeam  
116        http://dbpedia.org/ontology/Film  
117        http://dbpedia.org/ontology/City  
118   http://dbpedia.org/ontology/VideoGame  
119   http://dbpedia.org/ontology/VideoGame  

[120 rows x 3 columns]

In [ ]:
items_classes = []

for column in tqdm_notebook(column_items):
    item_classes = []
    for item in tqdm_notebook(column):
        items_classes.append(get_ontology_classes(item))

In [62]:
x = get_ontology_classes("Horse")

In [ ]:
# x

In [ ]:
# items_classes

#### DATAFRAME CREATION

In [161]:
items_classes_df = pd.DataFrame(columns=['item', 'classes'])

In [162]:
for items in tqdm_notebook(items_classes):
    res =  [ items[i] for i in (0, -1) ]
    items_classes_df = items_classes_df.append({'item' : res[0], 'classes': ";".join(map((lambda x: '"' + str(x) + '"'), res[1]))} , ignore_index=True)

In [165]:
mask = (items_classes_df['classes'] == '')
items_classes_df['classes'][mask] = '"' + items_classes_df2['item'] + '"'

item  \
0                                          The_Godfather   
1                                           Citizen_Kane   
2                                             Casablanca   
3                                     Lawrence_of_Arabia   
4      Dr_Strangelove_or_How_I_Learned_to_Stop_Worryi...   
5                                         Apocalypse_Now   
6                                  The_Godfather_Part_II   
7                                           Pulp_Fiction   
8                                   Its_a_Wonderful_Life   
9                                     Gone_with_the_Wind   
10                                           Raging_Bull   
11                                           Taxi_Driver   
12                                             Chinatown   
13                                          Blade_Runner   
14                                       Schindlers_List   
15                               ET_the_ExtraTerrestrial   
16                                            Annie_Hall   
17                                            Goodfellas   
18                                         The_Searchers   
19                                    North_by_Northwest   
20                                     The_Seven_Samurai   
21                                           Sunset_Blvd   
22                        One_Flew_over_the_Cuckoos_Nest   
23                                    A_Clockwork_Orange   
24                                         All_about_Eve   
25                                          The_Graduate   
26                                     On_the_Waterfront   
27                              The_Shawshank_Redemption   
28                                      Bonnie_and_Clyde   
29                                                 Fargo   
30                                   Saving_Private_Ryan   
31                          The_Bridge_on_the_River_Kwai   
32                                             High_Noon   
33      The_Lord_of_the_Rings_The_Fellowship_of_the_Ring   
34                               The_Night_of_the_Hunter   
35                                 To_Kill_a_Mockingbird   
36                                               Titanic   
37                                     The_Bicycle_Thief   
38                                           City_Lights   
39                                 The_Rules_of_the_Game   
40                                         The_400_Blows   
41                                       His_Girl_Friday   
42                                            Unforgiven   
43                               The_Battleship_Potemkin   
44                                                Brazil   
45                                    The_Sound_of_Music   
46                                                  8_12   
47                                            Breathless   
48                                       LA_Confidential   
49                                            Fight_Club   
50                                               Rashmon   
51                                       The_Deer_Hunter   
52                                             Nashville   
53                                           The_Shining   
54                                       West_Side_Story   
55                                    The_Grand_Illusion   
56                      The_Treasure_of_the_Sierra_Madre   
57                                          Forrest_Gump   
58          The_Lord_of_the_Rings_The_Return_of_the_King   
59                                               Sunrise   
60                                    Do_the_Right_Thing   
61                                                 Rocky   
62                                   The_Grapes_of_Wrath   
63                    Close_Encounters_of_the_Third_Kind   
64                                          Modern_Times   
65                                           Tokyo_Story   
66                              

In [167]:
items_classes_df.to_csv('items_classes_df.csv', index=False)

In [42]:
for s in column_items:
    print(*s)

['The Godfather', 'Citizen Kane', 'Casablanca', 'Lawrence of Arabia', 'Dr. Strangelove or: How I Learned to Stop Worrying and Love the Bomb', 'Apocalypse Now', 'The Godfather: Part II', 'Pulp Fiction', "It's a Wonderful Life", 'Gone with the Wind', 'Raging Bull', 'Taxi Driver', 'Chinatown', 'Blade Runner', "Schindler's List", 'E.T. the Extra-Terrestrial', 'Annie Hall', 'Goodfellas', 'The Searchers', 'North by Northwest', 'The Seven Samurai', 'Sunset Blvd.', "One Flew over the Cuckoo's Nest", 'A Clockwork Orange', 'All about Eve', 'The Graduate', 'On the Waterfront', 'The Shawshank Redemption', 'Bonnie and Clyde', 'Fargo', 'Saving Private Ryan', 'The Bridge on the River Kwai', 'High Noon', 'The Lord of the Rings: The Fellowship of the Ring', 'The Night of the Hunter', 'To Kill a Mockingbird', 'Titanic', 'The Bicycle Thief', 'City Lights', 'The Rules of the Game', 'The 400 Blows', 'His Girl Friday', 'Unforgiven', 'The Battleship Potemkin', 'Brazil', 'The Sound of Music', '8 1/2', 'Breath

#### PREPROCESS DF

In [ ]:
def preporcess_item(df):
    re.sub('[^A-Za-z0-9 ]+', '', word)

In [9]:
def replace_space(word):
    try:
        return word.replace(" ", "_")
    except:
        return word

In [10]:
def remove_special_characters(word):
    return re.sub('[^A-Za-z0-9 ]+', '', word)

In [11]:
def get_ontology_classes(item):
    sparql = SPARQLWrapper("http://dbpedia.org/sparql")
    sparql.setQuery("select distinct ?class where { dbr:"+item+" a ?class.}")
    sparql.setReturnFormat(JSON)
    results = sparql.query().convert()
 
    return [result["class"]["value"] for result in results["results"]["bindings"] 
            if 'http://dbpedia.org/ontology' in result["class"]["value"]]

In [12]:
def get_classes(df, column_id):
    column = df.iloc[ : , column_id]
    dbpednia_classes = cells = []
    
    for index, value in tqdm(column.items()):
        cell = remove_special_characters(value)
        cell = replace_space(cell)
        dbpednia_classes.append(get_ontology_classes(cell))
        cells.append(cell)
        
    return dbpednia_classes, cells

In [17]:
def process_tables(row):
    table_id = row["table_id"]
    column_id = row["column_id"]
    print(table_id, '###', column_id)
    df = pd.read_csv(os.path.join(tables_dir, table_id + ".csv"))
    dbpednia_classes, cells = get_classes(df, column_id)
    
    row["dbpednia_classes"] = dbpednia_classes
    row["cells"] = cells
    
    return row

In [18]:
df_targets = df_targets.progress_apply(process_tables, axis=1)
df_targets




  0%|                                                            | 0/109 [00:00<?, ?it/s]

10579449_0_1681126353774891032 ### 1






0it [00:00, ?it/s]



1it [00:00,  5.25it/s]



3it [00:00,  6.30it/s]



5it [00:00,  7.36it/s]



7it [00:00,  8.30it/s]



9it [00:00,  9.25it/s]



11it [00:01, 10.10it/s]



13it [00:01, 10.45it/s]



15it [00:01, 10.93it/s]



17it [00:01, 11.35it/s]



19it [00:01, 11.74it/s]



21it [00:01, 11.46it/s]



  2%|▉                                                   | 2/109 [00:01<01:39,  1.08it/s]

10579449_0_1681126353774891032 ### 1






0it [00:00, ?it/s]



2it [00:00, 12.66it/s]



4it [00:00, 12.80it/s]



6it [00:00, 12.41it/s]



8it [00:00, 12.51it/s]



10it [00:00, 12.59it/s]



12it [00:00, 12.67it/s]



14it [00:01, 12.39it/s]



16it [00:01, 12.29it/s]



18it [00:01, 12.45it/s]



21it [00:01, 12.53it/s]



  3%|█▍                                                  | 3/109 [00:03<02:02,  1.16s/it]

...





0it [00:00, ?it/s]



2it [00:00, 12.84it/s]



4it [00:00, 12.75it/s]



5it [00:00, 11.32it/s]



7it [00:00, 10.84it/s]



8it [00:00, 10.44it/s]



10it [00:00, 10.82it/s]



12it [00:01, 11.14it/s]



14it [00:01, 11.34it/s]



16it [00:01, 11.23it/s]



18it [00:01, 11.54it/s]



20it [00:01, 11.83it/s]



22it [00:01, 11.96it/s]



24it [00:02, 12.00it/s]



26it [00:02, 12.03it/s]



28it [00:02, 12.02it/s]



30it [00:02, 11.31it/s]



32it [00:02, 11.56it/s]



34it [00:02, 11.49it/s]



36it [00:03, 11.75it/s]



38it [00:03, 11.94it/s]



40it [00:03, 12.08it/s]



42it [00:03, 12.10it/s]



44it [00:03, 12.29it/s]



46it [00:03, 12.34it/s]



48it [00:04, 12.21it/s]



50it [00:04, 12.27it/s]



52it [00:04, 12.08it/s]



54it [00:04, 11.24it/s]



56it [00:04, 11.38it/s]



58it [00:04, 11.69it/s]



60it [00:05, 11.91it/s]



62it [00:05, 11.81it/s]



64it [00:05, 11.81it/s]



66it [00:05, 11.24it/s]



68it [00:05, 11.36it/s]



70it [00:06, 10.95it/s]



72it [0

26310680_0_5150772059999313798 ### 1






0it [00:00, ?it/s]



2it [00:00, 11.64it/s]



3it [00:00, 11.05it/s]



5it [00:00, 11.48it/s]



7it [00:00,  7.84it/s]



9it [00:01,  8.67it/s]



11it [00:01,  9.33it/s]



13it [00:01, 10.16it/s]



15it [00:01, 10.56it/s]



17it [00:01, 10.97it/s]



19it [00:01, 11.38it/s]



21it [00:02, 11.66it/s]



23it [00:02, 11.35it/s]



25it [00:02, 10.19it/s]



27it [00:02,  9.81it/s]



29it [00:02, 10.25it/s]



31it [00:03, 10.91it/s]



33it [00:12,  1.44s/it]



35it [00:12,  1.03s/it]



36it [00:12,  1.23it/s]



38it [00:12,  1.69it/s]



40it [00:13,  2.25it/s]



42it [00:13,  2.98it/s]



44it [00:13,  3.86it/s]



46it [00:13,  4.89it/s]



48it [00:13,  5.95it/s]



50it [00:13,  6.91it/s]



52it [00:13,  8.01it/s]



54it [00:14,  8.99it/s]



56it [00:14,  9.62it/s]



58it [00:14, 10.38it/s]



60it [00:14, 10.46it/s]



62it [00:14, 10.87it/s]



64it [00:15, 10.34it/s]



66it [00:15, 10.92it/s]



68it [00:15, 11.21it/s]



70it [00:15, 11.42it/s]



72it [0

TypeError: ('expected string or bytes-like object', 'occurred at index 27')





256it [00:59, 11.95it/s]